# Cleaning of 930, analyze how cleaning affects residual profile

In [1]:
# data source https://gridemissions.s3.us-east-2.amazonaws.com/EBA_elec.csv.gz

In [3]:
import numpy as np
import pandas as pd

import plotly.express as px
import plotly.graph_objects as go

import datetime as dt

In [4]:
%reload_ext autoreload
%autoreload 2

# Tell python where to look for modules. 
# Depending on how your jupyter handles working directories, this may not be needed.
import sys
sys.path.append('../../hourly-egrid/')

from src.visualization import day_hour_heatmap
from src.eia930 import fuel_code_map, reformat_chalendar, load_chalendar
from src.load_data import download_chalendar_files

/Users/gailin.pease/miniconda3/envs/hourly_egrid/lib/python3.9/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.9.1dev-CAPI-1.14.1) is incompatible with the GEOS version PyGEOS was compiled with (3.9.1-CAPI-1.14.2). Conversions between both will be slow.
  warnings.warn(


In [6]:
year = 2020

In [7]:
# Download data if not exists
download_chalendar_files()

EBA_elec.csv already downloaded
EBA_raw.csv already downloaded


In [8]:
# Note: cleaned file written by 930_lag.py
original = load_chalendar("../data/eia930/chalendar/EBA_adjusted_rolling.csv", year=year)

Filtering
Expanding cols
Dropping and renaming


In [9]:
cleaned = load_chalendar("../data/eia930/chalendar/EBA_adjusted_elec.csv", year=year)

Filtering
Expanding cols
Dropping and renaming


In [115]:
cems = pd.read_csv(f"../data/output/cems_{year}_cleaned_20220505.csv", index_col=0, parse_dates=['operating_datetime_utc'])
cems = cems.rename(columns={"operating_datetime_utc":"datetime_utc"})

/var/folders/mr/3dcnnc3153j6s05bmdwr0r0h0000gq/T/ipykernel_21044/2146096207.py:1: DtypeWarning:

Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.



# Visualize residual in one large BA

In [12]:
cleaned.head()

datetime_utc              variable  generation   BA fuel
0 2020-01-01 00:00:00+00:00  EBA.AEC-ALL.NG.COL.H   59.449007  AEC  COL
1 2020-01-01 01:00:00+00:00  EBA.AEC-ALL.NG.COL.H   57.441636  AEC  COL
2 2020-01-01 02:00:00+00:00  EBA.AEC-ALL.NG.COL.H   38.705315  AEC  COL
3 2020-01-01 03:00:00+00:00  EBA.AEC-ALL.NG.COL.H   72.992780  AEC  COL
4 2020-01-01 04:00:00+00:00  EBA.AEC-ALL.NG.COL.H   62.330264  AEC  COL

In [13]:
ba = "CISO"

ba_dat = cleaned.loc[cleaned["BA"] == ba, ["generation","fuel","datetime_utc"]].copy().rename(columns={"generation":"cleaned_gen"})
ba_dat = ba_dat.merge(\
    original.loc[original["BA"]==ba, ["generation","fuel","datetime_utc"]].copy().rename(columns={"generation":"original_gen"}),\
    how='left', on=["fuel","datetime_utc"])

In [127]:
#px.line(ba_dat, x="datetime_utc", y=["cleaned_gen","original_gen"], color="fuel")

In [15]:
# 930 fuel types are COL, NG, OIL, WAT, SUN, WND, OTH
# Chalendar adds two others: BIO, GEO in cleaned data, only in CISO
cleaned.fuel.unique()

array(['COL', 'NG', 'NUC', 'OIL', 'OTH', 'SUN', 'WAT', 'WND', 'GEO',
       'BIO'], dtype=object)

In [116]:
cems["fuel"] = cems["energy_source_code"].map(fuel_code_map)

In [122]:

# aggregate by either BA or physical BA, either way, make naming consistent
cems_aggregated = cems.groupby(["datetime_utc","ba_code_physical","fuel"]).sum()["net_generation_mwh"].reset_index().rename(columns={"ba_code_physical":"ba_code"})

# Plot residual 

In [123]:
#cems_fuels = cems_aggregated.fuel.unique() # includes SUN for some reason, dont' want that
cems_fuels = ["COL","NG","OIL","OTH"]

In [120]:
cleaned.BA.unique()

array(['AEC', 'AECI', 'AZPS', 'CISO', 'CPLE', 'CPLW', 'DUK', 'EEI',
       'ERCO', 'FMPP', 'FPC', 'GRID', 'GVL', 'IPCO', 'ISNE', 'JEA',
       'LDWP', 'LGEE', 'MISO', 'NEVP', 'NWMT', 'NYIS', 'OVEC', 'PACE',
       'PACW', 'PGE', 'PJM', 'PNM', 'PSCO', 'PSEI', 'SC', 'SCEG', 'SEC',
       'SOCO', 'SRP', 'SWPP', 'TEC', 'TEPC', 'TVA', 'WACM', 'WALC', 'AVA',
       'AVRN', 'BANC', 'BPAT', 'DEAA', 'EPE', 'FPL', 'GRIF', 'HGMA',
       'HST', 'IID', 'TAL', 'TIDC', 'NSB', 'AESO', 'CEN', 'CFE', 'GRMA',
       'IESO', 'NBSO', 'SPA', 'SPC', 'BCHA', 'CHPD', 'DOPD', 'GCPD',
       'HQT', 'MHEB', 'SCL', 'SEPA', 'TPWR', 'WAUW', 'YAD', 'GWA', 'WWA'],
      dtype=object)

In [125]:
ba = "PJM"

ba_dat = cleaned.loc[cleaned["BA"] == ba, ["generation","fuel","datetime_utc"]].copy().rename(columns={"generation":"cleaned_gen"})
ba_dat = ba_dat.merge(\
    original.loc[original["BA"]==ba, ["generation","fuel","datetime_utc"]].copy().rename(columns={"generation":"original_gen"}),\
    how='left', on=["fuel","datetime_utc"])

# add cems data
cems_ba = cems_aggregated.loc[cems_aggregated["ba_code"]==ba].copy()\
    .rename(columns={"net_generation_mwh":"cems_gen","operating_datetime_utc":"index","ba_code":"BA"})
ba_dat = ba_dat.merge(cems_ba, how='left', on=['fuel','datetime_utc'])

# Only want to show fuels in cems 
ba_dat = ba_dat[ba_dat.fuel.isin(cems_fuels)]

px.line(ba_dat, x="datetime_utc", y=["cleaned_gen","original_gen","cems_gen"], facet_col="fuel", facet_col_wrap=2)

In [126]:
ba = "MISO"
use = cleaned

toshow = []
for fuel in cems_fuels:
    cleaned_baf = use[(use.fuel==fuel) & (use.BA==ba)]
    cleaned_cems = cems_aggregated[(cems_aggregated.fuel==fuel) & (cems_aggregated.ba_code==ba)]
    dif = cleaned_baf.set_index("datetime_utc").generation - cleaned_cems.set_index("datetime_utc").net_generation_mwh
    fig, times = day_hour_heatmap(dif, year=year)
    toshow.append(fig)
    # map, times = day_hour_heatmap(cleaned_baf - cems_baf)

fig = px.imshow(np.stack(toshow), facet_col=0, facet_col_wrap=1,color_continuous_scale="RdBu", \
    width=1000, height=600, x=times, color_continuous_midpoint=0, \
    title=f"{ba}", template='plotly_white')

# Set facet names to fuels
fig.for_each_annotation(lambda a: a.update(text=cems_fuels[int(a.text.split("=")[-1])]))

# Calculate all residuals

In [24]:
residuals = pd.DataFrame()

# Calculate all residuals 
bas = np.union1d(cleaned.BA.unique(), cems_aggregated.ba_code.unique())
for ba in bas:
    print(f"{ba}...", end="")
    for fuel in cems_fuels:
        cleaned_baf = cleaned[(cleaned.fuel==fuel) & (cleaned.BA==ba)]
        cleaned_cems = cems_aggregated[(cems_aggregated.fuel==fuel) & (cems_aggregated.ba_code==ba)]
        dif = cleaned_baf.set_index("datetime_utc").generation - cleaned_cems.set_index("datetime_utc").net_generation_mwh
        dif = dif.rename("residual").to_frame()
        dif["BA"] = ba
        dif["fuel"] = fuel
        residuals = pd.concat([residuals,dif])

AEC...AECI...AESO...AVA...AVRN...AZPS...BANC...BCHA...BPAT...CEN...CFE...CHPD...CISO...CPLE...CPLW...CSTO...DEAA...DOPD...DUK...EEI...EPE...ERCO...FMPP...FPC...FPL...GCPD...GRID...GRIF...GRMA...GVL...GWA...HGMA...HQT...HST...IESO...IID...IPCO...ISNE...JEA...LDWP...LGEE...MHEB...MISO...NBSO...NEVP...NSB...NWMT...NYIS...OVEC...PACE...PACW...PGE...PJM...PNM...PSCO...PSEI...SC...SCEG...SCL...SEC...SEPA...SOCO...SPA...SPC...SRP...SWPP...TAL...TEC...TEPC...TIDC...TPWR...TVA...WACM...WALC...WAUW...WWA...YAD...

In [25]:
r = residuals.reset_index().set_index(["BA","fuel","datetime_utc"])
r = r.dropna()

# Metrics: 

* Number of sign changes in residual profile
* Mean residual profile
* % of days with negative residual
* Generation we expect in residual, based on difference between BA's 923 generation and 930 generation 

In [26]:
eia923 = pd.read_csv(f"../data/output/eia923_clean_{year}_20220502")

In [68]:
# Calculate difference between EIA-923 (expected annual 930 generation) and CEMS: this is the expected magnitude of the residual 
# group by fuel and BA
eia923["fuel"] = eia923["energy_source_code"].map(fuel_code_map)
net_gen_923 = (eia923.groupby(["ba_code","fuel"]).sum()).reset_index()
net_gen_923 = net_gen_923.pivot(index="ba_code",columns="fuel", values="net_generation_mwh").drop(columns=["SUN"])

# difference from CEMS 
cems_by_fuel = cems_aggregated.groupby(["ba_code","fuel"]).sum().reset_index().pivot(index="ba_code",columns="fuel",values="net_generation_mwh").drop(columns="SUN")

expected_residual = net_gen_923 - cems_by_fuel

expected_residual_as_percent = expected_residual/net_gen_923
expected_residual_as_percent_of_total = expected_residual.div(net_gen_923.sum(axis='columns'), axis='index')

In [75]:
px.bar(expected_residual, x=expected_residual.index, y=["COL","NG","OIL","OTH"], title="Expected residual (annual MWh)")

In [72]:
px.bar(expected_residual_as_percent, x=expected_residual_as_percent.index, y=["COL","NG","OIL","OTH"], title="Expected residual (percent of annual generation by fuel type)")

In [76]:
px.bar(expected_residual_as_percent_of_total, x=expected_residual_as_percent_of_total.index,
    y=["COL","NG","OIL","OTH"],title="Expected residual (percent of total annual generation)")

In [106]:
# Compare expected and actual residuals
total_residual = residuals.groupby(["BA","fuel"]).sum().reset_index()
total_residual["what"] = "Actual (930-CEMS)"

e = expected_residual.melt(ignore_index=False).reset_index().rename(columns={"ba_code":"BA","value":"residual"})
e["what"] = "Expected (923-CEMS)"

total_residual = pd.concat([total_residual, e])
px.bar(total_residual, x="BA",y="residual",color="what",facet_col="fuel",facet_col_wrap=1, barmode='group', width=1500, height=1000)


In [107]:
ng = net_gen_923.melt(ignore_index=False).reset_index().rename(columns={"value":"923_by_fuel"})
total_residual = total_residual.merge(ng, how='left',left_on=["BA","fuel"], right_on=["ba_code","fuel"])

ng_tot = ng.groupby("ba_code").sum().rename(columns={"923_by_fuel":"923_total"})
total_residual = total_residual.merge(ng_tot, how='left', left_on='BA', right_index=True)

total_residual

BA fuel      residual                 what ba_code   923_by_fuel     923_total
0     AEC  COL -5.909145e+01    Actual (930-CEMS)     AEC  3.184340e+05  4.846521e+06
1     AEC   NG -2.188322e+05    Actual (930-CEMS)     AEC  4.528087e+06  4.846521e+06
2     AEC  OTH  0.000000e+00    Actual (930-CEMS)     AEC           NaN  4.846521e+06
3    AECI  COL -1.954827e+04    Actual (930-CEMS)    AECI  1.306415e+07  2.340813e+07
4    AECI   NG -2.751171e+06    Actual (930-CEMS)    AECI  1.034343e+07  2.340813e+07
..    ...  ...           ...                  ...     ...           ...           ...
407  TIDC  OTH           NaN  Expected (923-CEMS)    TIDC           NaN  1.501050e+06
408  TPWR  OTH           NaN  Expected (923-CEMS)    TPWR  3.114870e+05  3.114870e+05
409   TVA  OTH           NaN  Expected (923-CEMS)     TVA  1.277450e+06  7.509361e+07
410  WACM  OTH           NaN  Expected (923-CEMS)    WACM           NaN  3.254784e+07
411  WALC  OTH           NaN  Expected (923-CEMS)    WALC           NaN  6.592776e+06

[412 rows x 7 columns]

In [108]:
total_residual["residual_frac_of_fuel_gen"]  = total_residual["residual"]/total_residual["923_by_fuel"]
total_residual["residual_frac_of_gen"]  = total_residual["residual"]/total_residual["923_total"]


In [109]:
# Compare expected and actual residuals as percent of  923 generation 

px.bar(total_residual, x="BA",y="residual_frac_of_fuel_gen",color="what",facet_col="fuel",facet_col_wrap=1, barmode='group', 
    width=1500, height=1000, title="Residual as percent of generation by fuel")

In [111]:
# Compare expected and actual residuals as percent of  923 generation 

px.bar(total_residual, x="BA",y="residual_frac_of_gen",color="what",facet_col="fuel",facet_col_wrap=1, barmode='group', 
    width=1500, height=1000, title="Residual as percent of generation by fuel")

# Metrics per-BA and fuel

In [27]:
bas = r.index.get_level_values(0).unique()
fuels = r.index.get_level_values(1).unique()

summary_sign_change = pd.DataFrame(index=bas, columns=fuels) # df of ba, fuel

for ba in bas:
    for fuel in r.loc[(ba)].index.get_level_values(0).unique(): # some bas don't have all fuels
        target = r.loc[(ba,fuel),:]
        val = np.sign(target).diff().ne(0).sum()
        summary_sign_change.loc[ba,fuel] = val.to_numpy()[0]

summary_sign_change

fuel   COL    NG   OTH  OIL
BA                         
AEC    175   812   NaN  NaN
AECI  2155   453   NaN  NaN
AVA    NaN   403   NaN  NaN
AVRN   NaN   591   NaN  NaN
AZPS     7   355   NaN  NaN
BANC   NaN   301   NaN  NaN
BPAT   NaN    69   NaN  NaN
CISO   NaN   256  1217  NaN
CPLE   340   994     1    1
DEAA   NaN   710   NaN  NaN
DUK    865   139   NaN  NaN
EEI    791    44   NaN  NaN
EPE    NaN   753   NaN  NaN
ERCO   581   742    13  NaN
FMPP   566   167   NaN  NaN
FPC    242   348   NaN   29
FPL    NaN   124   NaN  127
GRIF   NaN   321   NaN  NaN
GVL    454   338   964  NaN
IID    NaN  1071   NaN  NaN
IPCO   NaN   214   NaN  NaN
ISNE   113    63     1  265
JEA      7  1068   NaN  NaN
LDWP  1016   442   NaN  NaN
LGEE   154   197   NaN  NaN
MISO     6   577     1    1
NEVP   119   578   NaN  NaN
NWMT    85  3466   NaN  NaN
NYIS     6   539   NaN  113
OVEC   731   NaN   NaN  NaN
PACE     7    57   NaN  NaN
PACW   NaN     7   NaN  NaN
PGE      9    61   NaN  NaN
PJM    131   208   NaN   19
PNM    177   855   NaN  NaN
PSCO     1    61   NaN  NaN
PSEI   NaN    17   NaN  NaN
SC     883   771   NaN    2
SCEG  1080   981   NaN  NaN
SEC    586   543   NaN  NaN
SOCO   482  1483     1   25
SRP    315   401   NaN  NaN
SWPP   215   759   NaN   87
TAL    NaN   383   NaN  NaN
TEC    159   572   NaN  NaN
TEPC    55   525   NaN  NaN
TIDC   NaN  1578   NaN  NaN
TVA    181    66   NaN    1
WACM    77     1   NaN  NaN
WALC     1    29   NaN  NaN

In [27]:
bas = r.index.get_level_values(0).unique()
fuels = r.index.get_level_values(1).unique()

summary_mean = pd.DataFrame(index=bas, columns=fuels) # df of ba, fuel

for ba in bas:
    for fuel in r.loc[(ba)].index.get_level_values(0).unique(): # some bas don't have all fuels
        target = r.loc[(ba,fuel),:]
        val = target.mean()
        summary_mean.loc[ba,fuel] = val.to_numpy()[0]

summary_mean

fuel          COL           NG         OTH          OIL
BA                                                     
AEC       0.03782   -24.849583         NaN          NaN
AECI    -2.165411  -324.117276         NaN          NaN
AVA           NaN     6.953406         NaN          NaN
AVRN          NaN   -86.431693         NaN          NaN
AZPS  -888.552165   265.262562         NaN          NaN
BANC          NaN   193.555769         NaN          NaN
BPAT          NaN  -449.967714         NaN          NaN
CISO          NaN   1661.05998  -25.602259          NaN
CPLE   147.588958   -17.947805   890.95558    43.224217
DEAA          NaN    -20.72181         NaN          NaN
DUK    -45.416707   -649.74649         NaN          NaN
EEI     -54.48598   -26.722253         NaN          NaN
EPE           NaN     -4.60068         NaN          NaN
ERCO   226.476406  -388.304094   23.818071          NaN
FMPP     5.851937   208.160947         NaN          NaN
FPC    424.298834  -376.733202         NaN    19.151066
FPL           NaN  -819.507898         NaN   -396.17211
GRIF          NaN   -10.303284         NaN          NaN
GVL     -1.178789     0.147945   -1.177139          NaN
IID           NaN     4.432797         NaN          NaN
IPCO          NaN    15.655264         NaN          NaN
ISNE     3.633605    558.12454  555.698476   -32.962896
JEA    272.612663   -23.455421         NaN          NaN
LDWP     0.343819   134.556857         NaN          NaN
LGEE   133.569933     266.8716         NaN          NaN
MISO -1462.400465   475.870835  728.773161  3007.108602
NEVP   -14.233665    20.015517         NaN          NaN
NWMT    73.534813     6.564626         NaN          NaN
NYIS  -243.271816  -241.331146         NaN   637.739083
OVEC  -233.573837          NaN         NaN          NaN
PACE -1052.911357    86.839667         NaN          NaN
PACW          NaN  -302.833208         NaN          NaN
PGE   -458.031751  -482.607455         NaN          NaN
PJM   2195.452836  3310.507007         NaN   230.103032
PNM    129.188193    -7.879897         NaN          NaN
PSCO    826.12216   444.731831         NaN          NaN
PSEI          NaN   314.600862         NaN          NaN
SC     -33.479562   -19.272774         NaN     3.777193
SCEG  -119.038425   110.285486         NaN          NaN
SEC     -9.989025   164.864796         NaN          NaN
SOCO   -50.414247   190.813694  305.323832    16.934556
SRP    -21.018687  -155.543853         NaN          NaN
SWPP   400.315263    414.43344         NaN    73.475115
TAL           NaN    41.120522         NaN          NaN
TEC     -0.388746  -172.600137         NaN          NaN
TEPC  -372.280072    47.608926         NaN          NaN
TIDC          NaN     0.551984         NaN          NaN
TVA    225.922224 -1107.325068         NaN          1.0
WACM  -670.867401  -496.413982         NaN          NaN
WALC   862.393202  -475.016076         NaN          NaN

In [44]:
bas = r.index.get_level_values(0).unique()
fuels = r.index.get_level_values(1).unique()

summary_lt_0 = pd.DataFrame(index=bas, columns=fuels) # df of ba, fuel

for ba in bas:
    for fuel in r.loc[(ba)].index.get_level_values(0).unique(): # some bas don't have all fuels
        target = r.loc[(ba,fuel),:]
        val = (target < 0).residual.sum()/len(target)
        summary_lt_0.loc[ba,fuel] = val

summary_lt_0

fuel       COL        NG       OTH       OIL
BA                                          
AEC   0.737401  0.617111       NaN       NaN
AECI  0.488722  0.862207       NaN       NaN
AVA        NaN  0.619633       NaN       NaN
AVRN       NaN  0.797173       NaN       NaN
AZPS  0.994861  0.289829       NaN       NaN
BANC       NaN  0.132976       NaN       NaN
BPAT       NaN  0.983751       NaN       NaN
CISO       NaN   0.01242  0.896271       NaN
CPLE  0.326149  0.514751       0.0      0.04
DEAA       NaN  0.775364       NaN       NaN
DUK   0.623533  0.934389       NaN       NaN
EEI   0.570289  0.857741       NaN       NaN
EPE        NaN  0.550986       NaN       NaN
ERCO  0.364776  0.576327  0.026482       NaN
FMPP  0.448115  0.125299       NaN       NaN
FPC   0.229778  0.794965       NaN  0.478261
FPL        NaN  0.813418       NaN  0.906171
GRIF       NaN  0.783914       NaN       NaN
GVL   0.756861  0.382634  0.640943       NaN
IID        NaN  0.409512       NaN       NaN
IPCO       NaN  0.222904       NaN       NaN
ISNE  0.106874   0.11949       0.0  0.528221
JEA   0.010902  0.530357       NaN       NaN
LDWP   0.59074  0.309201       NaN       NaN
LGEE   0.21802  0.124317       NaN       NaN
MISO  0.889509   0.36519       0.0       0.0
NEVP   0.87096  0.499658       NaN       NaN
NWMT  0.107664  0.380762       NaN       NaN
NYIS   0.90604  0.656681       NaN  0.036324
OVEC  0.708053       NaN       NaN       NaN
PACE  0.994531  0.186624       NaN       NaN
PACW       NaN  0.999481       NaN       NaN
PGE   0.989595  0.978611       NaN       NaN
PJM   0.031097  0.077458       NaN  0.006336
PNM   0.156483  0.534414       NaN       NaN
PSCO       0.0  0.044093       NaN       NaN
PSEI       NaN  0.013168       NaN       NaN
SC    0.553024  0.571478       NaN  0.117647
SCEG  0.754687  0.308463       NaN       NaN
SEC   0.370205  0.132036       NaN       NaN
SOCO  0.625812  0.408019       0.0  0.220532
SRP   0.754349  0.640196       NaN       NaN
SWPP  0.254386  0.305423       NaN  0.269807
TAL        NaN  0.146258       NaN       NaN
TEC   0.419682  0.720241       NaN       NaN
TEPC  0.984277    0.4955       NaN       NaN
TIDC       NaN  0.469804       NaN       NaN
TVA   0.209089  0.967308       NaN       0.0
WACM  0.989404       1.0       NaN       NaN
WALC       0.0  0.993734       NaN       NaN

# Plot some generation residuals

In [128]:
# Note: the figure created here is very large, so leave out of git commit by commenting.

#px.line(residuals, x=residuals.index, y='residual', color='BA', facet_col='fuel', facet_col_wrap=1,width=1500, height=1000)